In [1]:
import pandas as pd

In [44]:
df = pd.read_csv("artworks.csv")

In [45]:
df.shape

(110618, 30)

In [46]:
df.head()

_id  acquisition_year acquisition_mode date_creation  \
0  150000000022692            1949.0            Achat  [avant 1949]   
1  150000001616310               NaN              Don   2003 - 2005   
2  150000000369068            2011.0            Achat          2004   
3  150000000369087            2011.0            Achat   2009 - 2010   
4  150000000454622            2011.0              Don          2009   

         type  ensemble_id             domain  \
0  individual          NaN           Peinture   
1  individual          NaN  Domaine non saisi   
2  individual          NaN       Objet/Design   
3  individual          NaN       Objet/Design   
4  individual          NaN       Objet/Design   

                                  domain_leaf domain_deno_for_grid  \
0                                    Peinture             Peinture   
1                                         NaN    Domaine non saisi   
2                                      Chaise         Objet/Design   
3  Audio-visuel,informatique, comm. et repro.         Objet/Design   
4                                Objet/Design         Objet/Design   

                              domain_description_mst        ...         \
0                                    Huile sur toile        ...          
1                                                NaN        ...          
2  Chaise|Chaise de récupération, béquille en aci...        ...          
3  série de 4 clés USB|Clés en métal, technologie...        ...          
4    Matériel de récupération, hanse en métal, béton        ...          

   recap_description                    all_realized_operations_history  \
0                NaN  2016/11/04 - 210I - Déplacement vers loc. inte...   
1                NaN                                                NaN   
2                NaN  2013/07/17 - 210I - Déplacement vers loc. inte...   
3                NaN  2013/07/12 - 210I - Déplacement vers loc. inte...   
4                NaN  2012/03/15 - 210I - Déplacement vers loc. inte...   

                                     hanging_history  \
0                                                NaN   
1                                                NaN   
2  2013/07/02 - 1N4 : Niveau 4 Centre|Dossier n° ...   
3  2013/07/02 - 1N4 : Niveau 4 Centre|Dossier n° ...   
4                                                NaN   

                                 hanging_history_m34  \
0  Phantastische Kunst des XX Jahrhunderts : Bâle...   
1                                                NaN   
2  Présentation des collections permanentes (coll...   
3  Présentation des collections permanentes (coll...   
4                                                NaN   

                           temporary_exhibitions_m30  \
0  Phantastische Kunst des XX Jahrhunderts : Bâle...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                            exposition_out_of_folder  \
0  Phantastische Kunst des XX Jahrhunderts : Bâle...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                                         expositions  \
0  Phantastische Kunst des XX Jahrhunderts : Bâle...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                         expositions_without_current             inscriptions  \
0  Phantastische Kunst des XX Jahrhunderts : Bâle...  S.B.DR. : g. de chirico   
1                                                NaN                            
2  Présentation des collections permanentes (col

## remove html tags

In [49]:
import re

def get_list_from_html(field):
    if(pd.isnull(field)):
        return []
    else:
        regex_item = re.compile('<li>(.*?)<\/li>', flags=re.S)
        tab = regex_item.split(str(field))
        new_tab = []
        for item in tab:
            if len(item) > 0 and 'ul>' not in item and item != '\n':
                new_tab.append(item)
        return new_tab

In [50]:
# df["operation_list"] = df["all_realized_operations_history"].apply(get_list_from_html)

In [51]:
df["operation_list"] = df["all_realized_operations_history"].apply(lambda x: str(x).split(";sep;"))

## remove no code cases from operation list

In [52]:
get_cleaned_list = lambda x : [i for i in x if len(i.split('-')) > 2]
remove_invalid_date = lambda x : [i for i in x if (int(i.split('-')[0][:4])>1678 and int(i.split('-')[0][:4])<2018)]
df["operation_list_clean"] = df["operation_list"].apply(get_cleaned_list).apply(remove_invalid_date)

In [15]:
# get_operation_between= lambda x : [i for i in x if (int(i.split('-')[0][:4])>1997 and int(i.split('-')[0][:4])<2001)]
# df["operation_list_1997_2000"] = df["operation_list_clean"].apply(get_operation_between)

## filter operation after 2001 && with code_loc only

In [68]:
code_loc = ["210I","211I","216I","220I", "221I","241I","260I","261I","262I","299I","730I","750I","760I",\
           "210E","211E","220E","221E","230E","240E","241E","250E","260E","299E","242E", "244E","760E"]

In [54]:
# filter_operation = lambda x : [i for i in x if (int(i.split('-')[0][:4])>2000 and i.split(' - ')[1] in code_loc)]
filter_operation = lambda x : [i for i in x if (int(i.split('-')[0][:4])>2000) ]
df["operation_list_after_2001"] = df["operation_list_clean"].apply(filter_operation)

# select column

In [55]:
df_freq = df[["_id", "title_notice", "operation_list_after_2001"]]

In [56]:
df_freq.shape

(110618, 3)

In [57]:
df_freq["operation_times"] = df_freq["operation_list_after_2001"].apply(lambda x: len(x))

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [58]:
df_freq = df_freq[df_freq.operation_times != 0]

In [59]:
df_freq.shape

(108081, 4)

In [60]:
sum(df_freq["operation_times"])

528711

In [62]:
def print_code(opts):
    for opt in opts:
        print(opt.split(' - ')[1])

In [63]:
df_freq["operation_list_after_2001"].apply(print_code)

210I
210I
410
210I
221I
230E
431
210I
410
210I
210I
210I
210I
210I
210I
321
210I
221I
303
410
410
410
230E
210I
431
210I
210I
302
410
210I
730I
210I
221I
230E
210I
211I
302
410
210I
520
262I
210I
210I
213I
212I
210I
211I
210I
210I
210I
213I
212I
210I
210I
211I
210I
210I
210I
210I
220I
210I
210I
210I
220I
210I
210I
210I
304
210I
210I
210I
211I
302
210I
972
220I
210I
210I
210I
210I
301
210I
901
211I
210I
210I
210I
972
212I
210I
211I
210I
972
212I
210I
210I
210I
972
212I
210I
211I
210I
972
212I
210I
210I
210I
210I
210I
972
212I
210I
211I
210I
221I
302
230E
210I
210I
321
210I
210I
210I
972
212I
210I
901
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
210I
210I
220I
972
210I
210I
220I
972
210I
210I
220I
972
901
901
901
210I
210I
210I
213I
212I
210I
220I
972
972
210I
211I
211I
213I
212I
212I
212I
241I
211I
211I
210I
210I
210I
212I
210I
980
972
220I
211I
211I
213I
212I
212I
212I
241I
211I
211I
901
901
901
901
901
211I
211I
901
211I
901
211I
901
211I
901
211I
90

210I
210I
210I
210I
901
210I
210I
213I
212I
901
210I
210I
213I
212I
901
210I
210I
213I
212I
901
210I
210I
213I
212I
901
210I
210I
213I
212I
210I
210I
210I
210I
210I
210I
210I
210I
901
210I
210I
213I
212I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
220I
302
210I
410
210I
230E
210I
302
213I
410
212I
302
210I
410
210I
410
212I
306
210I
520
210I
980
410
210I
211I
431
431
210I
210I
306
212I
210I
980
410
410
211I
972
220I
210I
210I
211I
210I
210I
211I
210I
210I
210I
210I
210I
210I
210I
260I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
211I
244E
302
210I
210I
210I
210I
210I
211I
210I
210I
730I
210I
210I
306
210I
730I
210I
210I
210I
210I
730I
210I
210I
306
210I
730I
210I
210I
210I
210I
730I
210I
210I
210I
306
730I
210I
210I
210I
210I
730I
210I
210I
210I
306
730I
210I
210I
210I
210I
730I
210I
210I
306
210I
730I
210I
210I
210I
210I
730I
210I
210I
210I
306
730I
2

211I
210I
210I
210I
901
211I
210I
210I
901
211I
210I
210I
210I
901
211I
901
211I
901
211I
210I
210I
210I
901
211I
210I
210I
210I
901
211I
221I
302
230E
210I
210I
210I
901
211I
210I
210I
210I
210I
240E
210E
302
210I
211I
306
213I
212I
980
221I
240E
212I
212I
302
210I
210I
210I
213I
212I
221I
221I
240E
230E
210I
302
210I
210I
211I
306
211I
221I
302
230E
210I
210I
221I
210E
210I
210I
302
221I
240E
230E
302
221I
230E
302
213I
212I
210I
212I
221I
230E
211I
210I
302
321
221I
230E
302
210I
221I
240E
212I
212I
302
210I
210I
221I
230E
211I
302
210I
210I
210I
221I
230E
302
210I
306
210I
221I
230E
210I
302
210I
210I
210I
221I
230E
302
210I
240E
210E
302
210I
210I
212I
211I
306
210I
211I
212I
220I
972
210I
210I
210I
901
211I
901
211I
901
211I
221I
230E
302
221I
230E
302
210I
210I
210I
901
211I
221I
230E
302
221I
230E
302
210I
210I
210I
901
221I
230E
302
211I
211I
221I
230E
302
221I
230E
302
901
221I
230E
302
211I
211I
210I
210I
210I
901
221I
230E
302
211I
211I
210I
210I
210I
901
211I
901
211I
210I

230E
302
211I
211I
901
211I
901
211I
901
211I
213I
213I
212I
901
211I
901
211I
901
211I
901
211I
213I
212I
322
901
211I
901
211I
901
211I
901
211I
901
221I
230E
302
211I
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
210I
212I
211I
306
211I
213I
212I
322
221I
230E
302
221I
230E
210I
302
211I
306
213I
213I
212I
212I
212I
210I
901
211I
901
211I
901
211I
901
211I
901
211I
901
221I
230E
302
211I
211I
901
211I
901
211I
901
211I
901
221I
230E
302
211I
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
213I
212I
322
211I
306
211I
221I
230E
302
221I
230E
210I
302
211I
306
321
221I
230E
302
210I
221I
230E
221I
230E
302
213I
213I
212I
212I
212I
210I
210I
221I
230E
302
221I
230E
210I
302
221I
230E
210I
302
211I
306
213I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I
901
211I


210I
306
210I
211I
210I
305
730I
210I
306
210I
211I
210I
305
730I
210I
306
210I
211I
210I
210I
221I
230E
302
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
210I
210I
212I
210I
211I
221I
230E
210I
302
210I
210I
212I
210I
211I
210I
211I
210I
520
520
972
301
220I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
901
211I
210I
210I
221I
230E
302
210I
212I
210I
210I
211I
213I
221I
230E
210I
210I
901
211I
221I
230E
210I
210I
901
211I
210I
901
211I
210I
901
211I
210I
210I
210I
210I
901
210I
210I
901
210I
210I
901
210I
210I
901
210I
210I
901
210I
210I
901
210I
210I
901
210I
210I
901
210I
230E
302
210I
210I
210I
210I
302
210I
321
306
210I
211I
211I
211I
211I
211I
210I
210I
210I
210I
306
210I
213I
212I
210I
221I
240E
230E
302
210I
210I
210I
210I
210I
210I
306
211I
210I
210I
210I
210I
210I
210I
210I
21

...

210I
221I
230E
302
210I
210I
210I
221I
230E
302
210I
410
210I
213I
212I
211I
210I
221I
230E
302
210I
221I
230E
302
210I
410
210I
213I
212I
211I
210I
213I
212I
211I
210I
210I
306
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
211I
210I
210I
306
980
210I
210I
980
306
211I
210I
213I
212I
211I
210I
210I
980
210I
210I
980
306
211I
210I
213I
212I
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
980
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
211I
210I
210I
306
980
210I
210I
980
211I
980
211I
210I
210I
980
210I
210I
980
306
211I
210I
210I
980
210I
210I
980
306
211I
210I
321
306
210I
980
210I
306
210I
210I
210I
210I
210I
221I
230E
302
210I
321
210I
210I
410
210I
210I


306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
210I
306
213I
212I
213I
212I
212I
211I
306
211I
213I
212I
212I
211I
306
213I
213I
212I
213I
212I
212I
211I
306
213I
212I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
210I
306
221I
210I
230E
302
211I
306
211I
211I
306
221I
210I
230E
302
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
302
211I
306
211I
211I
306
221I
230E
210I
302
210I
212I
221I
210I
230E
302
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
221I
230E
210I
302
210I
213I
212I
221I
210I
230E
302
306
211I
211I
306
211I
211I
306
211I
306
211I
211I
306
211I
211I
306
221I
210I
230E
302
302
211I
306
211I
211I
306
221I
210I
230E
302
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
211I
306
211I
302
211I
306
221I
210I
230E
302
211I
306
211I
211I
306
221I
230E
210I
302
210I
213I
212I
221I
2

210I
210I
210I
211I
210I
210I
221I
230E
302
210I
213I
212I
210I
210I
306
980
220I
980
210I
210I
221I
230E
210I
213I
212I
210I
210I
306
980
220I
980
221I
230E
212I
212I
221I
230E
221I
230E
212I
972
220I
212I
210I
210I
210I
210I
210I
210I
210I
221I
230E
302
210I
306
210I
210I
210I
210I
210I
212I
210I
221I
212I
230E
212I
221I
230E
220I
972
213I
212I
220I
972
221I
230E
302
210I
210I
210I
213I
212I
210I
210I
210I
210I
210E
730I
212I
210I
210I
210I
221I
230E
302
221I
230E
302
221I
230E
302
210I
260I
221I
230E
210I
302
321
220I
972
211I
306
211I
211I
306
211I
901
213I
212I
210I
220I
212I
210I
210I
322
210I
210I
210I
212I
212I
210I
210I
210I
210I
211I
210I
210I
306
321
212I
980
210I
210I
210I
213I
212I
210I
210I
210I
520
213I
212I
321
210I
210I
210I
210I
210I
972
301
210I
220I
210I
210I
210I
306
410
210I
210I
211I
210I
210I
211I
213I
212I
980
210I
302
210I
210I
210I
221I
230E
302
210I
210I
211I
242E
241E
242E
241E
242E
241E
241E
242E
241E
242E
241E
242E
241E
242E
241E
242E
241E
241E
242E
241E


302
210I
211I
972
301
220I
210I
213I
212I
221I
230E
210I
302
213I
212I
221I
230E
210I
302
210I
211I
972
301
220I
210I
213I
212I
210I
210I
221I
230E
210I
302
213I
212I
221I
230E
210I
302
210I
211I
972
301
220I
210I
213I
212I
221I
230E
210I
302
213I
212I
221I
230E
210I
302
210I
211I
972
301
220I
901
210I
210I
213I
212I
210I
221I
230E
302
213I
212I
980
210I
301
211I
210I
260I
211I
210I
260I
221I
230E
211I
210I
260I
211I
210I
260I
210I
210I
211I
211I
210I
210I
210I
301
220I
210I
210I
730I
210I
306
730I
210I
210I
210I
210I
730I
210I
306
730I
210I
210I
210I
210I
730I
210I
306
730I
210I
210I
210I
210I
730I
306
210I
210I
210I
210I
210I
212I
210I
210I
980
730I
210I
210I
211I
210I
210I
212I
210I
210I
730I
980
210I
210I
210I
213I
212I
210I
210I
730I
980
210I
210I
221I
302
230E
210I
210I
210I
213I
212I
210I
210I
730I
980
210I
210I
220I
901
211I
301
901
211I
301
213I
212I
901
211I
301
213I
212I
901
211I
301
901
211I
301
901
211I
301
213I
212I
901
211I
301
211I
212I
901
211I
301
210I
210I
210I
212I


0         None
2         None
3         None
4         None
5         None
6         None
7         None
8         None
9         None
10        None
11        None
12        None
13        None
14        None
15        None
16        None
17        None
18        None
19        None
20        None
21        None
22        None
23        None
24        None
25        None
26        None
27        None
28        None
29        None
37        None
          ... 
110587    None
110588    None
110589    None
110590    None
110591    None
110592    None
110593    None
110594    None
110595    None
110596    None
110597    None
110598    None
110599    None
110600    None
110601    None
110602    None
110603    None
110605    None
110606    None
110607    None
110608    None
110609    None
110610    None
110611    None
110612    None
110613    None
110614    None
110615    None
110616    None
110617    None
Name: operation_list_after_2001, Length: 108081, dtype: object

## get opt field(date, code, opt_name, details), store into dict

In [64]:
def format_date(date):
    return date.replace("/00", "/01")

* Branche stockage : 
2AR
2B
2C
2DE
2F
2L
2M
2N
2P
2S
2V
2TR
* Branche ateliers : 
2EMB
2ENC
* Branche restauration : 
2R
2NR
2QUA
* Branche photo : 
2PHO
* Branche constats : 
2ALV 
2NALV
2CON

* Subbranch type storage : 
1B
1D
1E
1F
1I
1J
1K
1L
1M
1N3
1T
6B
* Subbranch type restoration :
1LTR
* Subbranch type photography / digitalization : 
1STUPHO
1SAV
1STUVID
* Subbranch type studios : 
1A
* Subbranch permanent exhibition spaces : 
1N4S
1N4R
1N4T
1N4E
1N4GALCONS
1N4GALPRO
1N5S
1N5R
1N5T
1N5E
* Subbranch temporary exhibition spaces :
1N0
1N1
1N4GAG
1N4GAL0
1N4GALMUS
1N6
1PIAZZA
1GALPHO
1GRANDESALLE

In [65]:
branches = {"PN_stockage": ["2A", "2B", "2C", "2DE", "2F", "2L", "2M", "2N", "2P", "2S", "2V", "2TR"],\
"PN_ateliers":["2EMB", "2ENC"],\
"PN_restauration":["2R", "2NR", "2QUA"],\
"PN_photo": ["2PHO"],\
"PN_constats": ["2ALV", "2NALV", "2CON"],\
"CPINTER_storage":["1B", "1D", "1E", "1F", "1I", "1J", "1K", "1L", "1M", "1N3", "1T", "6B"],\
"CPINTER_restoration":["1LTR"],\
"CPINTER_photo":["1STUPHO", "1SAV", "1STUVID"],\
"CPINTER_studio":["1A"],\
"CPPUB_perm": ["1N4S", "1N4R", "1N4T", "1N4E", "1N4GALCONS", "1N4GALPRO", "1N5S", "1N5R", "1N5T", "1N5E"],\
"CPPUB_tempo": ["1N0", "1N1", "1N4GAG", "1N4GAL0", "1N4GALMUS", "1N6", "1PIAZZA", "1GALPHO", "1GRANDESALLE"],\
}

In [66]:
external_branch = ["M20","M22","M25","M29","M32","M36","M99"]
deposit_branch = ["M10", "M11", "M19"]

In [67]:
def dict_mapper(pattern, dict_branch = branches):
    cand = []
    for cat, pat in dict_branch.items():
        if pattern in [pat_part[0:len(pattern)] for pat_part in pat]:
            cand += [cat]
    return cand

def get_branch(text, dict_branch = branches):
    branch_list = dict_mapper(text[0], dict_branch = dict_branch)
    if len(text) < 2 or branch_list == []:
        return "unknown"
    else:
        i = 1
        while(len(branch_list) > 1):
            i += 1
            if i>len(text):
                break
            branch_list = dict_mapper(text[0:i],dict_branch = dict_branch)
    if branch_list == []:
        j = len(text)
        while(len(branch_list) < 1):
            if j<0:
                return text
            j -= 1
            branch_list = dict_mapper(text[0:j],dict_branch = dict_branch)
    return branch_list[0]

In [69]:
import re
def get_branch_field(opt):
    if(opt.split(' - ')[1] in code_loc):
        if("I" in opt.split(" - ")[1]):
            return get_branch(opt.split(" - ")[3])
        else:
            opt_detail = "-".join(opt.split(" - ")[3:])
            if(any(s in opt_detail for s in external_branch)):
                return "EXPO"
            elif(any(s in opt_detail for s in deposit_branch)):
                return "DEPOT"
            else:
                return "unknown"
    else:
        return "nonlocation"

In [70]:
get_opt_field = lambda x : sorted([{"date": format_date(i.split(' - ')[0]), "opt_code":i.split(" - ")[1],\
                             "opt_name": i.split(" - ")[2], "opt_branch": get_branch_field(i),\
                            "opt_detail": "-".join(i.split(" - ")[3:])}\
                            for i in x], key=lambda d: d['date'])

In [71]:
def get_opt_prop(x):
    return [{"date": format_date(i.split(' - ')[0]), "opt_code":i.split(" - ")[1],\
             "opt_name": i.split(" - ")[2], "opt_branch": get_branch_field(i),\
            "opt_detail": "-".join(i.split(" - ")[3:])}\
            for i in x]

In [72]:
df_freq["opt_field"] = df_freq["operation_list_after_2001"].apply(get_opt_field)

In [78]:
list(df_freq)

['_id',
 'title_notice',
 'operation_list_after_2001',
 'operation_times',
 'opt_field',
 'opt_times']

In [79]:
df_freq=df_freq.drop(["operation_times","opt_times","operation_list_after_2001"], axis=1)

In [80]:
df_freq.to_json("artwork_operations_with_branch_complete.json", orient="records")

In [84]:
df_freq[:1].to_json("example_artwork_operations_with_branch.json", orient="records")

In [ ]:
pd.read_json

# clean date creation

In [5]:
import re
years_re = re.compile(r"\d{4}")
def clean_creation_date(creation_date):
    years = years_re.findall(str(creation_date))
    if len(years)>=1:
        return int(min(years))
    else:
        return None

df["date_creation"] = df["date_creation"].apply(clean_creation_date)